<a href="https://colab.research.google.com/github/Sunnnyyy16/Practice/blob/main/hospital_visualization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 동물병원 데이터

## 데이터 로딩

In [1]:
from google.colab import drive
drive.mount('/gdrive')

Mounted at /gdrive


In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [3]:
!cp /gdrive/MyDrive/Petom/csv_files/hospital.csv ./

In [4]:
hospital = pd.read_csv('hospital.csv', encoding='utf-8')
hospital['도로명우편번호']=hospital['도로명우편번호'].astype(str)
hospital.head()

Unnamed: 0 상세영업상태명          소재지전화                     도로명전체주소 도로명우편번호  \
0           0      정상       571-9114   광주광역시 북구 양일로305번길 8 (일곡동)   61040   
1           1      정상   062-574-7975  광주광역시 북구 하서로 371, 1층 (양산동)   61074   
2           2      정상       224-7582    광주광역시 북구 서하로 319-1 (오치동)   61124   
3           3      정상  062) 419-7582       광주광역시 북구 중문로 74 (우산동)   61172   
4           4      정상   062-571-0011     광주광역시 북구 하백로5번길 1 (매곡동)   61066   

           name         lon        lat region  
0        일곡동물병원  126.894285  35.203171  광주광역시  
1      참좋은 동물병원  126.870562  35.208094  광주광역시  
2      김앤강 동물병원  126.912668  35.187089  광주광역시  
3    빛고을 동물의료센터  126.917727  35.179105  광주광역시  
4  24시 언제나 동물병원  126.887535  35.187886  광주광역시

In [5]:
hospital.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3528 entries, 0 to 3527
Data columns (total 9 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Unnamed: 0  3528 non-null   int64  
 1   상세영업상태명     3528 non-null   object 
 2   소재지전화       3528 non-null   object 
 3   도로명전체주소     3528 non-null   object 
 4   도로명우편번호     3528 non-null   object 
 5   name        3528 non-null   object 
 6   lon         3528 non-null   float64
 7   lat         3528 non-null   float64
 8   region      3528 non-null   object 
dtypes: float64(2), int64(1), object(6)
memory usage: 248.2+ KB


In [6]:
hospital.isnull().sum()

Unnamed: 0    0
상세영업상태명       0
소재지전화         0
도로명전체주소       0
도로명우편번호       0
name          0
lon           0
lat           0
region        0
dtype: int64

In [7]:
hospital['region'].value_counts()

경기도        935
서울특별시      840
부산광역시      237
경상남도       204
인천광역시      176
경상북도       160
대구광역시      149
전라북도       110
강원도        108
충청남도       107
광주광역시       94
제주특별자치도     88
대전광역시       87
전라남도        84
충청북도        77
울산광역시       52
세종특별자치시     20
Name: region, dtype: int64

# 동물병원 데이터 시각화-folium

## 서울시 동물병원 지도 시각화

In [9]:
import folium
from folium.plugins import MarkerCluster

sub_df = hospital[hospital['region']=='서울특별시'].reset_index()

center = [37.541, 126.986]
m_s = folium.Map(
    location=[center[0], center[1]],
    zoom_start=12
)

coords = sub_df[['lat', 'lon','name']]


marker_cluster = MarkerCluster().add_to(m_s)

for lat, lon, name in zip(coords['lat'], coords['lon'], coords['name']):
    folium.Marker([lat, lon], tooltip = name, icon = folium.Icon(color="red")).add_to(marker_cluster)
m_s

In [ ]:
# m_s.save('map.html')

# pydeck 지도시각화

In [ ]:
# from google.colab import output
# output.enable_custom_widget_manager()

In [10]:
!pip install pydeck

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.3 MB 7.4 MB/s 
     |████████████████████████████████| 1.6 MB 49.1 MB/s 


In [11]:
MAPBOX_API_KEY ='pk.eyJ1IjoibGFuZHN1biIsImEiOiJjbDdvcHIwbm8yZG1iM3BvZnMzenpvMjA4In0.YKw6kRcMWgVyDLhoZFkC9w'

In [12]:
import pydeck as pdk

In [13]:
data=hospital[['소재지전화','도로명전체주소','name','lat','lon']]
data.head()

소재지전화                     도로명전체주소          name        lat  \
0       571-9114   광주광역시 북구 양일로305번길 8 (일곡동)        일곡동물병원  35.203171   
1   062-574-7975  광주광역시 북구 하서로 371, 1층 (양산동)      참좋은 동물병원  35.208094   
2       224-7582    광주광역시 북구 서하로 319-1 (오치동)      김앤강 동물병원  35.187089   
3  062) 419-7582       광주광역시 북구 중문로 74 (우산동)    빛고을 동물의료센터  35.179105   
4   062-571-0011     광주광역시 북구 하백로5번길 1 (매곡동)  24시 언제나 동물병원  35.187886   

          lon  
0  126.894285  
1  126.870562  
2  126.912668  
3  126.917727  
4  126.887535

In [14]:
data.to_json('data.json')

In [15]:
layer = pdk.Layer(
    'ScatterplotLayer',
    data,
    pickable=True,
    opacity=0.8,
    stroked=True,
    filled=True,
    get_position='[lon, lat]',
    get_radius=100,
    get_fill_color=[255, 120, 120],
    get_line_color=[0, 0, 0],    
    auto_highlight=True
)

center = [126.986, 37.565]
view_state = pdk.ViewState(
    longitude=center[0],
    latitude=center[1],
    zoom=12)

r = pdk.Deck(layers=[layer],initial_view_state=view_state, tooltip={"text": "{name}\n{도로명전체주소}"}, map_style='road')

<IPython.core.display.Javascript object>

'<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />\n    <title>pydeck</title>\n        <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>\n        <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />\n    <script src=\'https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.5.*/dist/index.js\'></script>\n    <style>\n    body {\n  margin: 0;\n  padding: 0;\n  overflow: hidden;\n}\n\n#deck-map-container {\n  width: 100%;\n  height: 100%;\n  background-color: black;\n}\n\n#map {\n  pointer-events: none;\n  height: 100%;\n  width: 100%;\n  position: absolute;\n  z-index: 1;\n}\n\n#deckgl-overlay {\n  z-index: 2;\n  background: none;\n}\n\n#deck-map-wrapper {\n  width: 100%;\n  height: 100%;\n}\n\n#deck-container {\n  width: 100v

In [18]:
import pydeck as pdk
import pandas as pd


# Icon load
ICON_URL = 'https://uxwing.com/wp-content/themes/uxwing/download/location-travel-map/pin-location-icon.png'

icon_data = {
    "url": ICON_URL,
    "width": 128,
    "height": 128,
    "anchorY": 128,
}

data = hospital[['소재지전화','도로명전체주소','name','lat','lon']]
data["icon_data"] = None
for i in data.index:
    data["icon_data"][i] = icon_data

center = [126.986, 37.565]
view_state = pdk.ViewState(
    longitude=center[0],
    latitude=center[1],
    zoom=12)

icon_layer = pdk.Layer(
    type="IconLayer",
    data=data,
    get_icon="icon_data",
    get_size=2,
    size_scale=10,
    get_position=["lon", "lat"],
    pickable=True,
    opacity=0.8
)

r = pdk.Deck(layers=[icon_layer], initial_view_state=view_state,  tooltip={"text": "{name}\n{소재지전화}\n{도로명전체주소}"}, map_style='road')
r.to_html("hospital_icon.html")

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app.launch_new_instance()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


<IPython.core.display.Javascript object>

'<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />\n    <title>pydeck</title>\n        <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>\n        <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />\n    <script src=\'https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.5.*/dist/index.js\'></script>\n    <style>\n    body {\n  margin: 0;\n  padding: 0;\n  overflow: hidden;\n}\n\n#deck-map-container {\n  width: 100%;\n  height: 100%;\n  background-color: black;\n}\n\n#map {\n  pointer-events: none;\n  height: 100%;\n  width: 100%;\n  position: absolute;\n  z-index: 1;\n}\n\n#deckgl-overlay {\n  z-index: 2;\n  background: none;\n}\n\n#deck-map-wrapper {\n  width: 100%;\n  height: 100%;\n}\n\n#deck-container {\n  width: 100v

## pydeck 연습예제

In [20]:
import pydeck as pdk
import pandas as pd
import math

SCATTERPLOT_LAYER_DATA = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/website/bart-stations.json"
df = pd.read_json(SCATTERPLOT_LAYER_DATA)

# Use pandas to calculate additional data
df["exits_radius"] = df["exits"].apply(lambda exits_count: math.sqrt(exits_count))

# Define a layer to display on a map
layer = pdk.Layer(
    "ScatterplotLayer",
    df,
    pickable=True,
    opacity=0.8,
    stroked=True,
    filled=True,
    radius_scale=6,
    radius_min_pixels=1,
    radius_max_pixels=100,
    line_width_min_pixels=1,
    get_position="coordinates",
    get_radius="exits_radius",
    get_fill_color=[255, 140, 0],
    get_line_color=[0, 0, 0],
)

# Set the viewport location
view_state = pdk.ViewState(latitude=37.7749295, longitude=-122.4194155, zoom=10, bearing=0, pitch=0)

# Render
r = pdk.Deck(layers=[layer], initial_view_state=view_state, tooltip={"text": "{name}\n{address}"})
r.to_html("scatterplot_layer.html")

<IPython.core.display.Javascript object>

'<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />\n    <title>pydeck</title>\n        <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>\n        <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />\n    <script src=\'https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.5.*/dist/index.js\'></script>\n    <style>\n    body {\n  margin: 0;\n  padding: 0;\n  overflow: hidden;\n}\n\n#deck-map-container {\n  width: 100%;\n  height: 100%;\n  background-color: black;\n}\n\n#map {\n  pointer-events: none;\n  height: 100%;\n  width: 100%;\n  position: absolute;\n  z-index: 1;\n}\n\n#deckgl-overlay {\n  z-index: 2;\n  background: none;\n}\n\n#deck-map-wrapper {\n  width: 100%;\n  height: 100%;\n}\n\n#deck-container {\n  width: 100v

In [ ]:
df.head()

name code  \
0                     Lafayette (LAFY)   LF   
1  12th St. Oakland City Center (12TH)   12   
2              16th St. Mission (16TH)   16   
3              19th St. Oakland (19TH)   19   
4              24th St. Mission (24TH)   24   

                                       address  entries  exits  \
0      3601 Deer Hill Road, Lafayette CA 94549     3481   3616   
1              1245 Broadway, Oakland CA 94612    13418  13547   
2  2000 Mission Street, San Francisco CA 94110    12409  12351   
3              1900 Broadway, Oakland CA 94612    13108  13090   
4  2800 Mission Street, San Francisco CA 94110    12817  12529   

                coordinates  exits_radius  
0  [-122.123801, 37.893394]     60.133186  
1  [-122.271604, 37.803664]    116.391580  
2  [-122.419694, 37.765062]    111.135053  
3   [-122.269029, 37.80787]    114.411538  
4  [-122.418466, 37.752254]    111.933016

아이콘사이트: https://uxwing.com/add-map-location-icon/

In [21]:
import pydeck as pdk
import pandas as pd


# Data from OpenStreetMap, accessed via osmpy
DATA_URL = "https://raw.githubusercontent.com/ajduberstein/geo_datasets/master/biergartens.json"
ICON_URL = "https://upload.wikimedia.org/wikipedia/commons/c/c4/Projet_bi%C3%A8re_logo_v2.png"


icon_data = {
    # Icon from Wikimedia, used the Creative Commons Attribution-Share Alike 3.0
    # Unported, 2.5 Generic, 2.0 Generic and 1.0 Generic licenses
    "url": ICON_URL,
    "width": 128,
    "height": 128,
    "anchorY": 128,
}

data = pd.read_json(DATA_URL)
data["icon_data"] = None
for i in data.index:
    data["icon_data"][i] = icon_data

view_state = pdk.data_utils.compute_view(data[["lon", "lat"]], 0.1)

icon_layer = pdk.Layer(
    type="IconLayer",
    data=data,
    get_icon="icon_data",
    get_size=2,
    size_scale=10,
    get_position=["lon", "lat"],
    pickable=True,
)

r = pdk.Deck(layers=[icon_layer], initial_view_state=view_state, tooltip={"text": "{tags}"},map_style='light')
r.to_html("icon_layer.html")

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


<IPython.core.display.Javascript object>

'<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />\n    <title>pydeck</title>\n        <script src="https://api.tiles.mapbox.com/mapbox-gl-js/v1.13.0/mapbox-gl.js"></script>\n        <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css" />\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css" />\n    <script src=\'https://cdn.jsdelivr.net/npm/@deck.gl/jupyter-widget@~8.5.*/dist/index.js\'></script>\n    <style>\n    body {\n  margin: 0;\n  padding: 0;\n  overflow: hidden;\n}\n\n#deck-map-container {\n  width: 100%;\n  height: 100%;\n  background-color: black;\n}\n\n#map {\n  pointer-events: none;\n  height: 100%;\n  width: 100%;\n  position: absolute;\n  z-index: 1;\n}\n\n#deckgl-overlay {\n  z-index: 2;\n  background: none;\n}\n\n#deck-map-wrapper {\n  width: 100%;\n  height: 100%;\n}\n\n#deck-container {\n  width: 100v